In [1]:
from llama_index import (
    SimpleDirectoryReader,
    VectorStoreIndex,
    ServiceContext,
    set_global_tokenizer,
    load_index_from_storage,
)
from llama_index.llms import LlamaCPP
from llama_index.llms.llama_utils import (
    messages_to_prompt,
    completion_to_prompt,
)
from llama_index.vector_stores import ChromaVectorStore
from llama_index.storage.storage_context import StorageContext
from llama_index.embeddings import HuggingFaceEmbedding
from llama_index.query_engine import CitationQueryEngine
from llama_index.prompts import PromptTemplate

from IPython.display import Markdown, display

from transformers import AutoTokenizer

import os

import chromadb

/Users/peportier/miniforge3/envs/RAG_ENV/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/Users/peportier/miniforge3/envs/RAG_ENV/lib/python3.9/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


In [2]:
def messages_to_prompt(messages):
  prompt = ""
  for message in messages:
    if message.role == 'system':
      prompt += f"<|system|>\n{message.content}</s>\n"
    elif message.role == 'user':
      prompt += f"<|user|>\n{message.content}</s>\n"
    elif message.role == 'assistant':
      prompt += f"<|assistant|>\n{message.content}</s>\n"

  # ensure we start with a system prompt, insert blank if needed
  if not prompt.startswith("<|system|>\n"):
    prompt = "<|system|>\n</s>\n" + prompt

  # add final assistant prompt
  prompt = prompt + "<|assistant|>\n"

  return prompt

In [3]:
def completion_to_prompt(completion, system_prompt=None):
    prompt = ""
    system_prompt_str = system_prompt or """\
Vous fournissez avec soin des réponses précises, factuelles, réfléchies et nuancées, et vous êtes doué pour le raisonnement. \
Si vous pensez qu'il n'y a peut-être pas de bonne réponse, vous le dites. \
Ne soyez pas verbeux dans vos réponses, mais donnez des détails et des exemples lorsque cela peut aider à l'explication. \
"""
    prompt = f"<|system|>\n {system_prompt_str.strip()} </s>\n"
    prompt += f"<|user|>\n {completion} </s>\n"
    prompt += f"<|assistant|>\n"
    return prompt

In [4]:
llm = LlamaCPP(
    # You can pass in the URL to a GGML model to download it automatically
    model_url=None,
    # optionally, you can set the path to a pre-downloaded model instead of model_url
    # model_path='/Users/peportier/llm/a/a/mistral-7b-openorca.Q4_K_M.gguf',
    model_path='/Users/peportier/llm/a/a/zephyr-7b-beta.Q5_K_M.gguf',
    temperature=0.1,
    max_new_tokens=1024,
    # llama2 has a context window of 4096 tokens, but we set it lower to allow for some wiggle room
    context_window=3900,
    # kwargs to pass to __call__()
    # https://llama-cpp-python.readthedocs.io/en/latest/api-reference/#llama_cpp.Llama.__call__
    generate_kwargs={
        "temperature": 0.1,
        "mirostat_mode": 2,
    },
    # kwargs to pass to __init__()
    # https://llama-cpp-python.readthedocs.io/en/latest/api-reference/#llama_cpp.Llama.__init__
    # set to at least 1 to use GPU
    model_kwargs={
        "n_gpu_layers": 1,
    },
    # transform inputs into Llama2 format
    messages_to_prompt=messages_to_prompt,
    completion_to_prompt=completion_to_prompt,
    verbose=False,
)

llama_model_loader: loaded meta data with 21 key-value pairs and 291 tensors from /Users/peportier/llm/a/a/zephyr-7b-beta.Q5_K_M.gguf (version GGUF V3 (latest))
llama_model_loader: - tensor    0:                token_embd.weight q5_K     [  4096, 32000,     1,     1 ]
llama_model_loader: - tensor    1:           blk.0.attn_norm.weight f32      [  4096,     1,     1,     1 ]
llama_model_loader: - tensor    2:            blk.0.ffn_down.weight q6_K     [ 14336,  4096,     1,     1 ]
llama_model_loader: - tensor    3:            blk.0.ffn_gate.weight q5_K     [  4096, 14336,     1,     1 ]
llama_model_loader: - tensor    4:              blk.0.ffn_up.weight q5_K     [  4096, 14336,     1,     1 ]
llama_model_loader: - tensor    5:            blk.0.ffn_norm.weight f32      [  4096,     1,     1,     1 ]
llama_model_loader: - tensor    6:              blk.0.attn_k.weight q5_K     [  4096,  1024,     1,     1 ]
llama_model_loader: - tensor    7:         blk.0.attn_output.weight q5_K     [  409

In [5]:
model_name = "HuggingFaceH4/zephyr-7b-beta"
set_global_tokenizer(
    AutoTokenizer.from_pretrained(model_name).encode
)

In [6]:
# embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")
# embed_model = HuggingFaceEmbedding(model_name="sentence-transformers/all-MiniLM-L6-v2")
embed_model = HuggingFaceEmbedding(model_name="sentence-transformers/distiluse-base-multilingual-cased-v1")

/Users/peportier/miniforge3/envs/RAG_ENV/lib/python3.9/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


In [7]:
service_context = ServiceContext.from_defaults(
    llm=llm,
    embed_model=embed_model,
    chunk_size=512,
)

In [9]:
if not os.path.exists("./index_cera1"):
    documents = SimpleDirectoryReader("./docs/cera1").load_data()
    index = VectorStoreIndex.from_documents(
        documents, service_context=service_context
    )
    index.storage_context.persist(persist_dir="./index_cera1")
else:
    index = load_index_from_storage(
        StorageContext.from_defaults(persist_dir="./index_cera1"),
        service_context=service_context,
    )

In [ ]:
# db = chromadb.PersistentClient(path="./chroma_db")
# chroma_collection = db.get_or_create_collection("env")
# vector_store = ChromaVectorStore(chroma_collection=chroma_collection)
# storage_context = StorageContext.from_defaults(vector_store=vector_store)

In [ ]:
# # Create chroma index
# index = VectorStoreIndex.from_documents(
#     documents, storage_context=storage_context,
#     service_context=service_context
# )

In [10]:
text_qa_template_str_fr = (
  "<|system|>: Vous êtes un assistant IA qui répond à la question posée à la fin en utilisant le contexte suivant. Toutes les informations factuelles que vous utilisez pour répondre proviennent exclusivement du contexte. Si vous ne connaissez pas la réponse, dites simplement que vous ne savez pas, n'essayez pas d'inventer une réponse. Veuillez répondre exclusivement en français. </s>\n"
  "<|user|>: {context_str}\n"
  "Question: {query_str} </s>\n"
  "<|assistant|>:"
)

text_qa_template = PromptTemplate(text_qa_template_str_fr)

refine_template_str_fr = (
  "<|user|>: La requête originale est la suivante : {query_str}\n"
  "Nous avons fourni une première réponse : {existing_answer}\n"
  "Nous avons la possibilité d'affiner la réponse existante (seulement si nécessaire) avec un peu plus de contexte ci-dessous.\n"
  "------------\n"
  "{context_msg}\n"
  "------------\n"
  "Compte tenu du nouveau contexte, la réponse initiale est affinée afin de mieux répondre à la requête. Si le contexte n'est pas utile, renvoyer la réponse originale. </s>\n"
  "<|assistant|>:"
)
refine_template = PromptTemplate(refine_template_str_fr)

In [11]:
query_engine = index.as_query_engine(
    text_qa_template=text_qa_template,
    refine_template=refine_template,
    #response_mode="compact",
    response_mode="refine",
    similarity_top_k=5,
    streaming=True)

In [12]:
def display_prompt_dict(prompts_dict):
    for k, p in prompts_dict.items():
        text_md = f"**Prompt Key**: {k}<br>" f"**Text:** <br>"
        display(Markdown(text_md))
        print(p.get_template())
        display(Markdown("<br><br>"))

In [13]:
display_prompt_dict(query_engine.get_prompts())

**Prompt Key**: response_synthesizer:text_qa_template<br>**Text:** <br>

<|system|>: Vous êtes un assistant IA qui répond à la question posée à la fin en utilisant le contexte suivant. Toutes les informations factuelles que vous utilisez pour répondre proviennent exclusivement du contexte. Si vous ne connaissez pas la réponse, dites simplement que vous ne savez pas, n'essayez pas d'inventer une réponse. Veuillez répondre exclusivement en français. </s>
<|user|>: {context_str}
Question: {query_str} </s>
<|assistant|>:


<br><br>

**Prompt Key**: response_synthesizer:refine_template<br>**Text:** <br>

<|user|>: La requête originale est la suivante : {query_str}
Nous avons fourni une première réponse : {existing_answer}
Nous avons la possibilité d'affiner la réponse existante (seulement si nécessaire) avec un peu plus de contexte ci-dessous.
------------
{context_msg}
------------
Compte tenu du nouveau contexte, la réponse initiale est affinée afin de mieux répondre à la requête. Si le contexte n'est pas utile, renvoyer la réponse originale. </s>
<|assistant|>:


<br><br>

In [27]:
%%time
response = query_engine.query('''Quels sont les offres commerciales de la Caisse d'Epargne Rhône Alpes en faveur de la transition environnementale ?''')
response.print_response_stream()

En complément de notre réponse initiale, la Caisse d'Epargne Rhône Alpes a récemment financé un projet ambitieux de construction de 44 centrales solaires pour le compte de Terr e et Lac, une société spécialisée dans la production d'énergies renouvelables. Le montant total de ce financement bancaire s'élève à 14,5 millions d'euros et permettra la construction de centrales photovoltaïques sur les toitures, ombrières de parking et sol principalement situées en Auvergne-Rhône-Alpes. Ces installations représentent une capacité totale de 12,5 MWc. La Caisse d'Epargne Rhône Alpes est une banque régionale coopérative qui joue un rôle prépondérant dans le financement de la transition environnementale sur son territoire. Elle accompagne les entreprises de toutes tailles, les projets structurants des collectivités territoriales et le développement des producteurs d'énergies renouvelables en vertu de son engagement au Contrat d'Utilité. Les clients particuliers avec des projets de rénovation bénéf

In [17]:
for node in response.source_nodes:
    print(node.metadata["file_name"])

88c623578b.txt
bdc7145c09.pdf
7a4caa88da.pdf
0a235f3915.txt
bdc7145c09.pdf


In [28]:
for node in response.source_nodes:
    print(node.metadata["file_name"])
    print("\n---------------------------\n")
    display(Markdown(node.text))
    display(Markdown("---"))

88c623578b.txt

---------------------------



caissedepargnerhonealpes.fr/responsable-solidaire/)
Développement durable

Partager

# Engagée dans le Développement Durable

Agir pour la transition écologique

Réduire notre empreinte environnementale

Dans le cadre de sa démarche RSE, la Caisse d’Epargne Rhône Alpes poursuit une
politique volontariste pour répondre aux défis de la transition énergétique.
Elle accompagne l’ensemble de ses clients dans la transition vers une économie
plus durable, et agit à son niveau pour limiter l’impact de son activité sur
l’environnement.

## **Agir pour la transition écologique**

![](https://www.caissedepargnerhonealpes.fr/wp-
content/uploads/2021/11/491843054-2-806x1024.jpg)

**Accompagner la transformation des territoires**

Acteur majeur de l’Economie Locale, la Caisse d’Epargne Rhône Alpes joue
pleinement son rôle de grande banque coopérative régionale en favorisant le
financement d’infrastructures à impact positif sur notre territoire. Energies
renouvelables, ascenseurs valléens, rénovation énergétique de logements
sociaux, valorisation des déchets… elle accompagne de grands projets à haute
valeur environnementale.

---

efcbb5b260.txt

---------------------------



plus utile

Contribuer à la transition énergétique

Accompagner l'activité économique

Soutenir les projets solidaires

Favoriser l'emploi des jeunes

Régionale et coopérative, la Caisse d’Epargne Rhône Alpes s’engage au plus
près des besoins du territoire pour accompagner les transitions économiques,
environnementales et sociales. C’est le Contrat d’Utilité.​ Que représente-t-
il concrètement ? Voici quelques exemples de réalisation.

## Être utile, c'est aussi…

### **Cont** ribuer à la transition énergétique

![](https://www.caissedepargnerhonealpes.fr/wp-
content/uploads/2023/09/CERA_AFF-600x800mm_4visuels_v2_00004-768x1024.png)

La Caisse d'Epargne Rhône Alpes accompagne la **rénovation énergétique de plus
de 1 000 logements par an**. Les clients particuliers avec des projets de
rénovation bénéficient des [conseils](https://www.caisse-epargne.fr/rhone-
alpes/emprunter/maprimerenov/) de France Rénov’, partenaire de la Caisse
d’Epargne Rhône Alpes.

**Pour les entreprises et collectivités, la transition énergétique est un
enjeu majeur**.

...

Les clients particuliers avec des projets de
rénovation bénéficient des [conseils](https://www.caisse-epargne.fr/rhone-
alpes/emprunter/maprimerenov/) de France Rénov’, partenaire de la Caisse
d’Epargne Rhône Alpes.

**Pour les entreprises et collectivités, la transition énergétique est un
enjeu majeur**. La Caisse d'Epargne Rhône Alpes [accompagne leur démarche de
transformation](https://www.caisse-epargne.fr/rhone-
alpes/professionnels/conseils/choisir-solutions-durables-responsables/) via :

  * Des financements adaptés, comme le Prêt à Impact - une offre innovante de financement dont le taux d’intérêt est indexé sur des objectifs environnementaux et/ou sociétaux - ou encore une gamme de prêts « green » à disposition des acteurs économiques pour leur transition écologique, 
  * Des conseils et expertises sur-mesure selon les besoins et secteurs d’activité.

---

bdc7145c09.pdf

---------------------------



Ce financement s ’inscrit dans la feuille de route de la Caisse 
d’Epargne Rhône Alpes qui a mis au cœur de ses prio rités la transition énergétique et le 
financement des ENR à l’échelle de ses territoires.  » 
 
Sébastien Fenet , Directeur Général de Terre et Lac : « Depuis sa création, Terre et Lac accompagne 
les acteurs de notre région, entreprises, agriculte urs et collectivité locales dans la transition 
énergétique. Forts de cet ancrage territorial que n ous sommes fiers de partager avec notre 
partenaire bancaire la Caisse d’Epargne Rhône Alpes , nous contribuons ensemble au développement 
des énergies renouvelables avec la même préoccupati on : développer des projets respectueux de 
leur environnement en étroite collaboration avec le s habitants de notre territoire » 
 
 
À propos de la Caisse d’Epargne Rhône Alpes : 
La Caisse d’Epargne Rhône Alpes est une banque comm erciale, régionale et coopérative de plein exercice  présente sur 
cinq départements (Ain, Isère, Rhône, Savoie et Hau te-Savoie) et sur tous les métiers de la banque. El le agit au 
quotidien pour le développement de son territoire. 
Elle compte 1,4 million de clients, 458 000 sociéta ires, 3 000 collaborateurs, 280 agences.

---